In [2]:
import pandas as pd
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from scipy import stats
import matplotlib.pyplot as plt
from sklearn import cross_validation
from sklearn.cross_validation import cross_val_score
from sklearn.grid_search import RandomizedSearchCV
from scipy.stats import randint as sp_randint
from sklearn.ensemble import GradientBoostingClassifier
from scipy.stats import uniform
%matplotlib inline
plt.style.use('ggplot')

/usr/local/lib/python2.7/dist-packages/sklearn/cross_validation.py:44: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)
/usr/local/lib/python2.7/dist-packages/sklearn/grid_search.py:43: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. This module will be removed in 0.20.
  DeprecationWarning)


In [3]:
data_test = pd.read_csv("../data/raw/credit_test.csv", encoding='cp1251', sep=';')

In [4]:
data_test.head()

client_id gender  age marital_status job_position credit_sum  credit_month  \
0     170747      F   48            MAR          UMN   16558,00            10   
1     170748      M   29            MAR          SPC    7028,72             6   
2     170749      F   20            UNM          SPC   13019,00            10   
3     170750      F   41            MAR          SPC    9379,00            10   
4     170751      F   31            MAR          SPC   13990,00             6   

   tariff_id score_shk education     living_region  monthly_income  \
0       1.10  0,370409       GRD      ХАКАСИЯ РЕСП           34000   
1       1.40  0,377281       SCH   ОБЛ КЕМЕРОВСКАЯ           19000   
2       1.60  0,538515       SCH  ОБЛ БЕЛГОРОДСКАЯ           25000   
3       1.10  0,482520       GRD     ОБЛ ИРКУТСКАЯ           30000   
4       1.43  0,485914       GRD     ОБЛ КИРОВСКАЯ           20000   

   credit_count  overdue_credit_count  
0           2.0                   0.0  
1           3.0                   0.0  
2           1.0                   0.0  
3           0.0                   0.0  
4           2.0                   0.0

In [5]:
data_train = pd.read_csv("../data/raw/credit_train.csv", encoding='cp1251', sep=';')

In [12]:
data_train.head()

client_id gender  age marital_status job_position credit_sum  credit_month  \
0          1      M   48            MAR          UMN   59998,00            10   
1          2      F   28            MAR          UMN   10889,00             6   
2          3      M   32            MAR          SPC   10728,00            12   
3          4      F   27            DIV          SPC   12009,09            12   
4          5      M   45            MAR          SPC   16908,89            10   

   tariff_id score_shk education        living_region  monthly_income  \
0        1.6  0,770249       GRD   КРАСНОДАРСКИЙ КРАЙ         30000.0   
1        1.1  0,248514       GRD               МОСКВА         43000.0   
2        1.1  0,459589       SCH      ОБЛ САРАТОВСКАЯ         23000.0   
3        1.1  0,362536       GRD    ОБЛ ВОЛГОГРАДСКАЯ         17000.0   
4        1.1  0,421385       SCH  ЧЕЛЯБИНСКАЯ ОБЛАСТЬ         25000.0   

   credit_count  overdue_credit_count  open_account_flg  
0           1.0                   1.0                 0  
1           2.0                   0.0                 0  
2           5.0                   0.0                 0  
3           2.0                   0.0                 0  
4           1.0                   0.0                 0

In [77]:
def change(x):
    print(type(x))
    s = x.split(',')
    return s[0] + '.' + s[1]
    

In [81]:
def split_data(data_transformed):
    data = data_transformed.drop(['open_account_flg', 'client_id'], axis = 1)
    data = pd.get_dummies(data, columns=['education', 'job_position', 'marital_status', 'gender', 'tariff_id', 'living_region'])
    target = data_transformed['open_account_flg']
    data[['score_shk']] = data[['score_shk']].apply(lambda x: map(change, x))
    data[['score_shk']] = data[['score_shk']].apply(pd.to_numeric)
    x_train, x_val, y_train, y_val = cross_validation.train_test_split(data, target, test_size=0.2, random_state=123, stratify = target)
    return x_train, x_val, y_train, y_val

In [82]:
def transform_data(data):
    data_transformed = data
    data_transformed['gender'] = students['sex'] == "M"
    return data_transformed

In [83]:
x_train, x_val, y_train, y_val = split_data(data_train)

<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode'>
<type 'unicode

In [61]:
x = x_train['score_shk'].as_matrix()

In [64]:
x[0] + x[1]

u'0,4654620,645696'

In [57]:
rf_clf = RandomForestClassifier(class_weight = "balanced")
rf_param_dist ={"n_estimators" : np.arange(10, 100, 10),
                  "max_depth": sp_randint(1, 100),
                  "max_features": sp_randint(1, 370),
                  "min_samples_split": sp_randint(1, 100),
                  "min_samples_leaf": sp_randint(1, 100),
                  "max_features" : ["auto", "sqrt", "log2"],
                  "criterion": ["gini", "entropy"]}

n_iter_search = 250
rf_random_search = RandomizedSearchCV(rf_clf, param_distributions = rf_param_dist,
                                   n_iter = n_iter_search, random_state = 123, cv=5)
rf_random_search.fit(x_train, y_train)
rf_clf = rf_random_search.best_estimator_
rf_val_score = rf_clf.score(x_val, y_val)
print("Best randomized search score - %s" % rf_random_search.best_score_)
print("Validation score - %s" % rf_val_score)

ValueError: invalid literal for float(): 0,372187